In [1]:
import time
import random
import os

import matplotlib.pyplot as plt
import osmnx as ox
import networkx as nx
import folium
import geopandas as gpd
import shapely.geometry

import transit as tr

Задаем константы


In [2]:
GTFSpath = r"D:\Python_progs\Feeds\Klapeida" # Путь к папке с GTFS файлами
departure_time_input = "14:00:00" # Время отправления в формате HH:MM:SS
day = 'monday' # День недели
time_zero = time.time()
city_name = os.path.basename(GTFSpath)

plot_graph = False # Не работает
save_city_graph = False # Сохранять граф города в файл
plot_path_in_browser = False # Отобразить маршрут при помощи Folium в браузере
plot_path_folium = True # Отобразить маршрут при помощи Folium в Ipython Notebook

In [3]:
tr.validate_feed(GTFSpath) # Проверка корректности GTFS-фида

GTFS feed is valid.


True

Загружаем комбинированный граф GTFS и OSM

In [4]:
output_path = rf"D:\Python_progs\Output\{city_name}_graph.graphml" # Путь к файлу для сохранения графа города

G_combined, stops = tr.feed_to_graph(GTFSpath, departure_time_input, 
                                      day, duration_seconds=3600*8, read_shapes = False,
                                      save_to_csv = True, save_graphml = False, output_graph_path = output_path)

""" G_combined, stops = tr.feed_to_graph(GTFSpath, departure_time_input, 
                                      day, duration_seconds=3600*3, 
                                      save_to_csv = True, load_graphml = True, input_graph_path = output_path) """

GTFS data loaded
34345 of 72974 trips retained
Закончено формирование графа транспорта
Выпуклая оболочка построена, начинается загрузка графа улиц OSM в сети
Граф улиц загружен
Начинается соединение графов
Число узлов: 32002
Число ребер: 83208
Соединение завершено


' G_combined, stops = tr.feed_to_graph(GTFSpath, departure_time_input, \n                                      day, duration_seconds=3600*3, \n                                      save_to_csv = True, load_graphml = True, input_graph_path = output_path) '

Выбираем рандомные узлы графа для расчета времени в пути. 
По координатам потом удобно сверять время с Гугл картами/Яндексом  

p.s. Главное отключить метро :) 
p.p.s В гугл картах лучше сравнивать не время в пути, а время прибытия, т.к. они не показывают время ожидания



In [5]:
source = random.choice(list(G_combined.nodes))
target = random.choice(list(G_combined.nodes))

print("Source: ", source, "coordinates", G_combined.nodes[source]['y'], G_combined.nodes[source]['x'])
print("Target: ", target, "coordinates", G_combined.nodes[target]['y'], G_combined.nodes[target]['x'])

Source:  1838685852 coordinates 55.8828762 21.2225845
Target:  469488631 coordinates 55.517341 21.3193335


In [6]:
def main():
    sample_time = time.time()
    
    path, arrival_time, travel_time, used_routes = tr.time_dependent_dijkstra(
                            graph = G_combined, 
                            source = source, 
                            target = target, 
                            start_time = tr.parse_time_to_seconds(departure_time_input),
                            track_used_routes=True,
                        )

    print(f"Path: {path}")
    print('Used routes:', used_routes)
    print(f"Arrival time at destination: {tr.parse_seconds_to_time(arrival_time)} in {tr.parse_seconds_to_time(travel_time)}")

    print(f"Time elapsed: {time.time() - sample_time} seconds")

    return path, arrival_time, travel_time

path, arrival_time, travel_time = main()

Path: [1838685852, 1838685887, 4464602541, 2934022146, 2934022145, 2934022144, 2934022143, 2934022142, 7800214661, 2934022141, 2934022140, 2934022139, 2934022138, 2744638327, 1039743469, 2309165653, 59602483, 59602486, 1835746329, 1835746333, 7694.0, 7695, 7086, 7685, 7687, 7689, 4781, 4783, 4785, 4871, 271, 4829, 7273, 7618, 4320, 4370, 4368, 4366, 159, 163, 116, 4125, 4138, 138, 4894, 75, 73, 71, 3797, 69, 63, 2528466643, 1022295892, 4325325659, 5829543507, 5829543508, 4014293895, 2528466605, 2896595693, 2885304344, 64.0, 66, 40, 3856, 3852, 7225, 196, 4317, 6670, 6672, 6674, 6676, 7937, 8106, 8139, 7940, 3570381693, 2138687921, 2138687926, 2138687880, 1141222180, 1141222280, 450539735, 7673682923, 7673682921, 7673682919, 7673682924, 7673682928, 7673682931, 7673682933, 7673682935, 469488609, 1068908168, 1141222352, 4402461855, 2204753695, 1141157810, 4401101660, 450539745, 4401095617, 4401095596, 450539747, 450539749, 450539752, 4401093146, 450544547, 450539761, 3176865559, 469488631

In [7]:
G_path = nx.subgraph(G_combined, path)
print(G_path)
graph = nx.MultiDiGraph(G_path)

G_nodes, G_edges = ox.graph_to_gdfs(graph)

frame_center_lat = stops['stop_lat'].mean()
frame_center_lon = stops['stop_lon'].mean()

if plot_path_in_browser:
    tr.plot_path_browser(graph, stops)

m2 = folium.Map(location=[frame_center_lat, frame_center_lon], 
                zoom_start=12,
                width='100%', height='100%')

G_edges.explore(m = m2)

G_nodes.explore(m = m2,
                column = 'type',
                cmap = 'rainbow')

DiGraph with 109 nodes and 174 edges


In [8]:
sa_source = random.choice(list(G_combined.nodes))

In [9]:
polygon, points = tr.create_service_area(G_combined, sa_source, start_time=50000, cutoff = 1800, buffer_radius=100)
polygon2, points = tr.create_service_area(G_combined, sa_source, start_time=50120, cutoff = 1800, buffer_radius=100)
polygon3, points = tr.create_service_area(G_combined, sa_source, start_time=50240, cutoff = 1800, buffer_radius=100)

In [10]:
point = shapely.geometry.Point(G_combined.nodes[sa_source]['x'], G_combined.nodes[sa_source]['y'])
point_gdf = gpd.GeoDataFrame(geometry=[point])

frame_center_lat = stops['stop_lat'].mean()
frame_center_lon = stops['stop_lon'].mean()

m = folium.Map(location=[frame_center_lat, frame_center_lon], 
                zoom_start=12,
                width='100%', height='100%')

polygon.explore(m = m)
polygon2.explore(m = m, color = 'green')
polygon3.explore(m = m, color = 'red')

point_gdf.explore(m = m, color = 'red')

In [11]:
tr.calculate_edge_frequency(G_combined, 40000, 68000)

frame_center_lat = stops['stop_lat'].mean()
frame_center_lon = stops['stop_lon'].mean()

G_combined2 = nx.MultiDiGraph(G_combined)

G_nodes2, G_edges2 = ox.graph_to_gdfs(G_combined2)

filtered_nodes = G_nodes2[G_nodes2['type'] == 'transit']

filtered_edges = G_edges2[G_edges2['type'] == 'transit']

In [12]:
m = folium.Map(location=[frame_center_lat, frame_center_lon], 
                zoom_start=12,
                width='100%', height='100%')

filtered_nodes.explore(m = m, column = 'frequency', cmap = 'gnuplot', 
                       legend = True, scheme = 'Quantiles', k = 6)

filtered_edges.explore(m = m, column = 'frequency', cmap = 'gnuplot', 
                         legend = True, scheme = 'Quantiles', k = 6)

import cProfile
def main():
    G2_combined, stops2 = tr.feed_to_graph(GTFSpath, departure_time_input, 
                                      day, duration_seconds=3600*3, 
                                      save_to_csv = True, load_graphml = False,
                                      read_shapes = True)

cProfile.run("main()")

In [13]:
times_list = []
startt = tr.parse_time_to_seconds(departure_time_input)
endt = startt + 50000
for i in range(startt, endt, 300):
    try:
        path, arrival_time, travel_time = tr.time_dependent_dijkstra(
                                        graph = G_combined, 
                                        source = source, 
                                        target = target, 
                                        start_time = i,
                                        track_used_routes=False)
        print(travel_time)
                                    
        times_list.append(tuple([i, travel_time]))
    except Exception as e: 
        print(e)
        continue
    
print(times_list)

10777.086404554248
10477.086404554248
10177.086404554248
9877.086404554248
9577.086404554248
15476.710562224776
15176.710562224776
14876.710562224776
14576.710562224776
14276.710562224776
13976.710562224776
13676.710562224776
13376.710562224776
13076.710562224776
12776.710562224776
12476.710562224776
12176.710562224776
11876.710562224776
11576.710562224776
11276.710562224776
10976.710562224776
10676.710562224776
10376.710562224776
10076.710562224776
9776.710562224776
9476.710562224776
10976.710562224776
10676.710562224776
10376.710562224776
10076.710562224776
9776.710562224776
9476.710562224776
9176.710562224776
8876.710562224776
8576.710562224776
8276.710562224776
7976.710562224776
16449.651453582148
16149.651453582148
15849.651453582148
15549.651453582148
15249.651453582148
14949.651453582148
14649.651453582148
14349.651453582148
14049.651453582148
13749.651453582148
13449.651453582148
13149.651453582148
12849.651453582148
12549.651453582148
12249.651453582148
11949.651453582148
1164

In [14]:

plt.figure(figsize=(14,3))
plt.plot(*zip(*times_list))

plt.xlabel('Departure Time')
plt.ylabel('Travel Time')
plt.show()